In [13]:
# This is necessary to recognize the modules
import os
import sys


root_path = os.path.abspath(os.path.join(os.getcwd(), '../..'))
sys.path.append(root_path)


In [33]:
from plotly.subplots import make_subplots
import pandas as pd
import numpy as np
import plotly.graph_objects as go

from hummingbot.connector.connector_base import TradeType


def get_bt_candlestick_trace(df):
    df.index = pd.to_datetime(df.timestamp, unit='s')
    return go.Scatter(x=df.index,
                      y=df['close'],
                      mode='lines',
                      line=dict(color="blue"),
                      )


def get_pnl_trace(executors):
    pnl = [e.net_pnl_quote for e in executors]
    cum_pnl = np.cumsum(pnl)
    return go.Scatter(
        x=pd.to_datetime([e.close_timestamp for e in executors], unit="s"),
        y=cum_pnl,
        mode='lines',
        line=dict(color='gold', width=2, dash="dash"),
        name='Cumulative PNL'
    )


def get_default_layout(title=None, height=800, width=1800):
    layout = {
        "template": "plotly_dark",
        "plot_bgcolor": 'rgba(0, 0, 0, 0)',  # Transparent background
        "paper_bgcolor": 'rgba(0, 0, 0, 0.1)',  # Lighter shade for the paper
        "font": {"color": 'white', "size": 12},  # Consistent font color and size
        "height": height,
        "width": width,
        "margin": {"l": 20, "r": 20, "t": 50, "b": 20},
        "xaxis_rangeslider_visible": False,
        "hovermode": "x unified",
        "showlegend": False,
    }
    if title:
        layout["title"] = title
    return layout


def add_executors_trace(fig, executors, row, col):
    for executor in executors:
        entry_time = pd.to_datetime(executor.timestamp, unit='s')
        entry_price = executor.custom_info["current_position_average_price"]
        exit_time = pd.to_datetime(executor.close_timestamp, unit='s')
        exit_price = executor.custom_info["close_price"]
        name = "Buy Executor" if executor.config.side == TradeType.BUY else "Sell Executor"

        if executor.filled_amount_quote == 0:
            fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, entry_price], mode='lines',
                                     line=dict(color='grey', width=2, dash="dash"), name=name), row=row, col=col)
        else:
            if executor.net_pnl_quote > Decimal(0):
                fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, exit_price], mode='lines',
                                         line=dict(color='green', width=4), name=name), row=row, col=col)
            else:
                fig.add_trace(go.Scatter(x=[entry_time, exit_time], y=[entry_price, exit_price], mode='lines',
                                         line=dict(color='red', width=4), name=name), row=row, col=col)

    return fig


def create_backtesting_figure(df, executors, config):
    # Create subplots
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True,
                        vertical_spacing=0.02, subplot_titles=('Candlestick', 'PNL Quote'),
                        row_heights=[0.7, 0.3])

    # Add candlestick trace
    fig.add_trace(get_bt_candlestick_trace(df), row=1, col=1)

    # Add executors trace
    fig = add_executors_trace(fig, executors, row=1, col=1)

    # Add PNL trace
    fig.add_trace(get_pnl_trace(executors), row=2, col=1)

    # Apply the theme layout
    layout_settings = get_default_layout(f"Trading Pair: {config['trading_pair']}")
    layout_settings["showlegend"] = False
    fig.update_layout(**layout_settings)

    # Update axis properties
    fig.update_xaxes(rangeslider_visible=False, row=1, col=1)
    fig.update_xaxes(row=2, col=1)
    fig.update_yaxes(title_text="Price", row=1, col=1)
    fig.update_yaxes(title_text="PNL", row=2, col=1)
    return fig

In [34]:
import pickle

import pandas as pd
path = os.path.join(root_path, "research_notebooks", "xtreet_bb", "backtesting_results.pickle")

bt_results = pickle.load(open(path, 'rb'))

In [39]:
result = bt_results['xtreet_bb_binance_perpetual_1m_ADA-USDT_0.0_0.249_0.008_0.01_200_2.0_0.013525179856115217.yml']

In [44]:
import pandas as pd

results_df = pd.DataFrame([result["results"] for result in bt_results.values()])
results_df

net_pnl  net_pnl_quote  total_executors  \
0   -0.00275499    -2.75499021              137   
1   -0.01516589   -15.16588502              100   
2   -0.00007787    -0.07786584              100   
3   -0.11044877  -110.44877394              119   
4   -0.00135307    -1.35307041               87   
..          ...            ...              ...   
595 -0.02365573   -23.65573119              109   
596 -0.00091204    -0.91204308              128   
597  0.00262084     2.62083906               76   
598 -0.01997806   -19.97805555               91   
599   0.0034724     3.47239524               63   

     total_executors_with_position   total_volume  total_long  total_short  \
0                              133   8249.5896749          90           43   
1                               98 22830.94385212          53           45   
2                               98  2034.30545097          59           39   
3                              116 35274.88246567          67           49   
4                               84  1654.13917188          42           42   
..                             ...            ...         ...          ...   
595                            106    42811.02231          57           49   
596                            125   803.22935848          73           52   
597                             73  1145.96045516          38           35   
598                             88 15067.75511811          51           37   
599                             63 22804.12094402          36           27   

                                           close_types  accuracy_long  \
0                {'TAKE_PROFIT': 65, 'TIME_LIMIT': 72}     0.56666667   
1    {'STOP_LOSS': 3, 'TAKE_PROFIT': 38, 'TIME_LIMI...     0.62264151   
2                {'TAKE_PROFIT': 38, 'TIME_LIMIT': 62}     0.59322034   
3    {'STOP_LOSS': 10, 'TAKE_PROFIT': 58, 'TIME_LIM...      0.6119403   
4                {'TAKE_PROFIT': 46, 'TIME_LIMIT': 41}     0.71428571   
..                                                 ...            ...   
595  {'STOP_LOSS': 7, 'TAKE_PROFIT': 60, 'TIME_LIMI...     0.64912281   
596              {'TAKE_PROFIT': 69, 'TIME_LIMIT': 59}     0.56164384   
597              {'TAKE_PROFIT': 25, 'TIME_LIMIT': 51}     0.63157895   
598  {'STOP_LOSS': 6, 'TAKE_PROFIT': 29, 'TIME_LIMI...     0.60784314   
599  {'STOP_LOSS': 13, 'TAKE_PROFIT': 20, 'TIME_LIM...     0.52777778   

     accuracy_short  total_positions   accuracy  max_drawdown_usd  \
0        0.58139535              133 0.57142857       -5.86694795   
1        0.51111111               98 0.57142857      -22.17797244   
2        0.61538462               98 0.60204082       -2.56748382   
3         0.6122449              116 0.61206897     -123.70585871   
4        0.57142857               84 0.64285714       -2.29256304   
..              ...              ...        ...               ...   
595      0.71428571              106 0.67924528      -67.45288455   
596      0.61538462              125      0.584       -0.91161508   
597      0.65714286               73 0.64383562       -1.44789306   
598      0.45945946               88 0.54545455      -27.91297241   
599      0.74074074               63 0.61904762      -30.70075969   

     max_drawdown_pct  sharpe_ratio  profit_factor  win_signals  loss_signals  \
0         -0.00586534   -0.17687741     0.88259564           76            57   
1         -0.02213323   -0.41736442     0.86944916           56            42   
2         -0.00256699   -0.20864279     0.99130274           59            39   
3          -0.1254214   -1.39588048     0.52418536           71            45   
4         -0.00229229   -0.69353889     0.83337208           54            30   
..                ...           ...            ...          ...           ...   
595       -0.06734557   -0.59818812     0.85559845           72            34   
596       -0.00091171   -1.26367499      0.6903144           73            52   
597        -0.0014476  

In [45]:
import plotly.express as px

# Create a new column with custom hover text
results_df['custom_hover_text'] = results_df.apply(lambda row: f"""
Pair: {row['config']['trading_pair']}
<br>Volume: {row['total_volume']}
<br>PNL: {row['net_pnl_quote']}
<br>Close types: {row['close_types']}

Config:
<br>Id: {row['config']['id']}
<br>BB Length: {row['config']['bb_length']}
<br>BB Std: {row['config']['bb_std']}
<br>Take profit: {row['config']['take_profit']}
<br>Stop loss: {row['config']['stop_loss']}
<br>Time limit: {row['config']['time_limit']}
<br>DCA Spreads: {row['config']['dca_spreads']}
<br>DCA Amounts: {row['config']['dca_amounts_pct']}
""", axis=1)

# Create the scatter plot with the custom hover text
fig = px.scatter(
    results_df,
    x="total_volume",
    y="net_pnl_quote",
    color="trading_pair",  # Color by trading_pair
    hover_data={"custom_hover_text": True},  # Show the custom hover text
    color_discrete_sequence=px.colors.qualitative.Plotly,  # Optional: use a specific color sequence
    title="Net PNL Quote vs. Total Volume by Trading Pair"
)

# Show the figure
fig.show()


In [38]:
from decimal import Decimal

df = result["df"]
config = result["config"]
executors = result["executors"]


fig = create_backtesting_figure(
    df=df,
    executors=executors,
    config=config.dict())
# df.ta.bbands(length=config.bb_length, std=config.bb_std, append=True)
fig.add_trace(go.Scatter(x=df.index,
                         y=df[f"BBU_{config.bb_length}_{config.bb_std}"],
                         line=dict(color='lightblue', width=1))
              )
# fig.add_trace(go.Scatter(x=df.index,
#                          y=df[f"BBM_{config.bb_length}_{config.bb_std}"])
#               )
fig.add_trace(go.Scatter(x=df.index,
                         y=df[f"BBL_{config.bb_length}_{config.bb_std}"],
                         line=dict(color='lightblue', width=1))
                         )
fig.update_layout(width=1400)
fig.show()